In [213]:
include("simulator.jl")
dataset1 = get_dataset1()
dataset2 = get_dataset2()
;

## Another useful pair: CTT and CAZ

CTT alone gets stuck at a local optimum of 0100 instead of reaching its global optimum of 0111:

In [160]:
criticaltimes, trace = run_simulation(dataset2[:CTT], "0000")
plot_simulation(trace, criticaltimes)

Whereas CAZ quickly reaches its global optimum of 0110:

In [159]:
criticaltimes, trace = run_simulation(dataset2[:CAZ], "0000")
plot_simulation(trace, criticaltimes)

Exposing a population to CAZ and then CTT, we manage to reach CTT's global optimum of 0111:

In [171]:
criticaltimes, trace = run_simulation([(dataset2[:CTT], 1), (dataset2[:CAZ], 150), (dataset2[:CTT], 1050)], "0000")
plot_simulation(trace, criticaltimes)

## Modifying the carrying capacity

So far, we have been using a carrying capacity of 10^9 and a probability of mutation of 10^-8.

In [183]:
criticaltimes, trace = run_simulation(dataset1[3][6], "0000")
plot_simulation(trace, criticaltimes, ["0000","0001","0010","0100","1000","0110","0101","0111","1110"])

If we reduce the carrying capacity by several orders of magnitude (to 10^6), we see quite a bit more fluctuation between the simulations (useful to run this cell multiple times):

In [205]:
criticaltimes, trace = run_simulation(dataset1[3][6], "0000", K=1.0e6)
plot_simulation(trace, criticaltimes)

If we also increase the probability of mutation to 10^-5 to match our new carrying capacity, our simulation runs similarly to the above but on a shorter timescale.

In [206]:
criticaltimes, trace = run_simulation(dataset1[3][6], "0000", K=1.0e6, P_m=1.0e-5)
plot_simulation(trace, criticaltimes, ["0000","0001","0010","0100","1000","0110","0101","0111","1110"])

## Slowing down discovery of the global optimum

The most interesting case we have come across so far is that of ZOX:

In [217]:
criticaltimes, trace = run_simulation(dataset2[:ZOX], "0000", t=3000)
plot_simulation(trace, criticaltimes, ["0000","0010","0011","0111"])

The optimal genotype of 0111 first appears early on but takes around 2600 timesteps to attain dominance over 0011. This is caused by a unique situtation in which the growth rate of the optimal genotype (0111) is very similar to the growth rate of its closest intermediate (0011):
![ZOX](ZOX.png)
In this landscape, genotype 0011 has a growth rate of 2.683 while genotype 0111 has a growth rate of 2.688, a difference of only 0.005.

We can write some code to try and find similar situations:

In [220]:
ordering = get_genotypes(16)
mutational_neighbors = get_mutational_neighbors(ordering)
for (name, landscape) in eachcol(dataset2)
    for i in eachindex(landscape)
        for j in mutational_neighbors[i]
            diff = landscape[j] - landscape[i]
            if diff > 0 && diff < 0.01
                println(name, " ", ordering[i], " & ", ordering[j])
            end
        end
    end
end

AMP 0100 & 0110
AM 0000 & 0001
AM 1011 & 1001
ZOX 0011 & 0111
CRO 0110 & 1110
AMC 0111 & 0110
TZP 0011 & 0111


Taking the case of AM and genotypes 1011 and 1001, we can obtain a slow growth pattern if we start from genotype 1011 instead of 0000, and block genotypes 1101 and 1111. However, I can't think of any sequence of drugs that would cause these conditions to arise on their own.

In [228]:
landscape=copy(dataset2[:AM])
genotypes=get_genotypes(16)
landscape[findfirst(genotypes, "1101")] = 0
landscape[findfirst(genotypes, "1111")] = 0
criticaltimes, trace = run_simulation(landscape, "1011", t=3000)
plot_simulation(trace, criticaltimes)

Similarly, starting from genotype 0110 with landscape CRO and blocking 0100:

In [243]:
landscape = copy(dataset2[:CRO])
landscape[findfirst(genotypes, "0100")] = 0
criticaltimes, trace = run_simulation(landscape, "0110")
plot_simulation(trace, criticaltimes)

Incidentally, I've noticed that running simulations on CRO returns variable results (run this cell multiple times):

In [254]:
criticaltimes, trace = run_simulation(dataset2[:CRO], "0000")
plot_simulation(trace, criticaltimes)

There are multiple genotypes that may become dominant by the end of 1200 timesteps. The following runs 100 simulations and outputs the frequency of final dominant genotypes:

In [262]:
dominantgenotypes=[]
for i = 1:100
    criticaltimes, trace = run_simulation(dataset2[:CRO], "0000")
    push!(dominantgenotypes, genotypes[indmax(trace[1200,:])])
end
[(count(x -> x == u, dominantgenotypes), u) for u in unique(dominantgenotypes)]
    

3-element Array{Tuple{Int64,String},1}:
 (79, "1010")
 (16, "0011")
 (5, "0100") 